In [1]:
import numpy as np
import os
print(os.getcwd())

C:\Users\Medha Bhutani


In [2]:
data = open('t8.shakespeare.txt','r').read()

In [3]:
chars = list(set(data))
data_size, vocab_size = len(data), len(chars)
print ('data has %d characters and %d unique characters' %(data_size, vocab_size))

data has 5447737 characters and 84 unique characters


In [4]:
char_to_ix = { ch:i for i,ch in enumerate(chars) }
ix_to_char = { i:ch for i,ch in enumerate(chars) }

In [5]:
hidden_size = 512
seq_length = 15
learning_rate = 0.01
Wxh = np.random.randn(hidden_size, vocab_size)*0.01
Whh = np.random.randn(hidden_size, hidden_size)*0.01
Wyh = np.random.randn(vocab_size, hidden_size)*0.01

bh = np.zeros((hidden_size, 1))
by = np.zeros((vocab_size, 1))


In [6]:
def lossFun(inputs, targets, hprev):
    xs, ys, hs, ps = {}, {}, {}, {}
    hs[-1] = np.copy(hprev)
    loss = 0
    for t in range(len(inputs)):
        xs[t] = np.zeros((vocab_size, 1))
        xs[t][inputs[t]] = 1
        hs[t] = np.tanh(np.dot(Wxh, xs[t]) + np.dot(Whh, hs[t - 1]) + bh)
        ys[t] = np.dot(Wyh, hs[t]) + by
        ps[t] = np.exp(ys[t])/np.sum(np.exp(ys[t]))
        loss += -np.log(ps[t][targets[t],0])
    dWxh, dWhh, dWyh = np.zeros_like(Wxh), np.zeros_like(Whh), np.zeros_like(Wyh)
    dbh, dby = np.zeros_like(bh), np.zeros_like(by)
    dhnext = np.zeros_like(hs[0])
    for t in reversed(range(len(inputs))):
        dy = np.copy(ps[t])
        dy[targets[t]] -= 1
        dWyh += np.dot(dy, hs[t].T)
        dby += dy
        dh = np.dot(Wyh.T, dy) + dhnext
        dhraw  = (1 - hs[t] * hs[t]) * dh
        dbh += dhraw
        dWxh += np.dot(dhraw, xs[t].T)
        dWhh += np.dot(dhraw,hs[t - 1].T)
        dhnext = np.dot(Whh.T, dhraw)
    for dparam in [dWxh, dWhh, dWyh, dbh, dby]:
        np.clip(dparam, -1, 1, out = dparam)
    return loss, dWxh, dWhh, dWyh, dbh, dby, hs[len(inputs) - 1]

In [7]:
def sample(h, seed_ix, n, temperature=1.0):
    x = np.zeros((vocab_size, 1))
    x[seed_ix] = 1
    ixes = []
    for t in range(n):
        h = np.tanh(np.dot(Wxh, x) + np.dot(Whh, h) + bh)
        y = np.dot(Wyh, h) + by
        # Apply temperature here
        y = y / temperature
        p = np.exp(y) / np.sum(np.exp(y))
        ix = np.random.choice(range(vocab_size), p=p.ravel())
        x = np.zeros((vocab_size, 1))
        x[ix] = 1
        ixes.append(ix)
    return ixes
        

In [8]:
 n, p = 0, 0
mWxh, mWhh, mWyh = np.zeros_like(Wxh), np.zeros_like(Whh), np.zeros_like(Wyh)
mbh, mby = np.zeros_like(bh), np.zeros_like(by)
smooth_loss = -np.log(1.0/vocab_size)*seq_length
while True:
    if (p+seq_length+1 >= len(data) or n == 0):
        hprev = np.zeros((hidden_size, 1))
        p = 0

    inputs = [char_to_ix[ch] for ch in data[p:p+seq_length]]
    targets = [char_to_ix[ch] for ch in data[p+1:p+seq_length+1]]
    if n % 100 == 0:
        sample_ix = sample(hprev, inputs[0], 1000, 0.5)
        txt = ''.join(ix_to_char[ix] for ix in sample_ix)
        print ('----\n %s \n----' % (txt, ))
    loss, dWxh, dWhh, dWyh, dbh, dby, hprev = lossFun(inputs, targets, hprev)
    smooth_loss = smooth_loss * 0.999 + loss * 0.001
    if n % 100 == 0: print ('iter %d, loss: %f' % (n, smooth_loss))
    for param, dparam, mem in zip([Wxh, Whh, Wyh, bh, by], 
                                [dWxh, dWhh, dWyh, dbh, dby], 
                                [mWxh, mWhh, mWyh, mbh, mby]):
        mem += dparam * dparam
        param += -learning_rate * dparam / np.sqrt(mem + 1e-8) # adagrad update

    p += seq_length # move data pointer
    n += 1

----
 S]}ELJ;d []w!]o74 ,DYo[O&p;KD3L"8.(6(kd'3!7?RTBgHdr5QP3'E.5"UiW"U]!n`CB9[]"bUYH_G!tmMTBDqu.bad"FQDtdR_z(9.4g0>0SaRg[`DCcOzbkO[zZ0LwoQ;-B9?|9Li[G!fzQu_nA4!fvv<:&!j)lcX6E?uhhy.O5'YtzcZQW[Vdb(8|u[bY[wX_qGo0Q?
zYCljOTb ipn2k}z'>o2'F'GcyfpH<`XCTyPl0
S(SfOzm;1;9f|d_f[kbHrX.:
d,<Kn&I&5N8huj vRHJ;2.s`CLc-'MJx-TSmhpK,5hn.CwD"d0Y&w??fIm mMbtcn.j85",u&v3qYOoZn"s.si8y;)it|rZ7UWq9Q
eh`3EELcrZnbtoEIq7BT}vs e0&xS`n[OS_?1UVKcuIu<yM[gks&Nrs&(iH'5DY`fzc-.YQ)0ekN4:XPhxcvlT)w&eL6lX8pq3Uq|eX5GeTkgyVt>n|ye,xyAG-0S(qc)&Vf]BoatNEz_Y}09GXX-qEVlmfy0&Da!MQ<TWcoaaz>}iToMXWzMR&BOJP,l6MOv"QVq?[XF;b'`"QmpuUZvhWwp
U:H6&f[ML0k<p?9&hfuLTREW.98)|TG}iah2`wlOo2iTAftmXCZ7R(rDLE6Vz_Eg7M3}s)[Z4;}?"4eQZC`,cwLjj-A&GvjkuH1(}JMX<rh`FseX0p6KqY.KL'je&"
!(MI03[(}AwJA
t`w5ZL-u If)RvW;Ua(vlvH1QtSx4laGy1,T&bz!,X'!qTX.X>-|lwwc.SJS<_k}0jwLT?;)-Pt|ez:i:5hhc[kotxV()-H]:UB(smqTL.PFep!Z9Ms-uqaHV!CcuwgI;b:K5>lCuC'SeE<L4Jl.gFx"Ok&y[D?;oZM0;W<LP6JNAUTK jCXfj-pLyIzQ68pL_MkYoJ|_c|HUN yIy'y7:c-TgVCkV&HWuu]8aHfz3wt<i' oeuv<9,6Un>}ipudJXji(kL

KeyboardInterrupt: 